# EV Range vs. Price

In [4]:
import pandas as pd
import numpy as np
import altair as alt
import requests

In [5]:
df = pd.read_csv('vehicles.csv')

df.head()

/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (70,71,72,73,74,76,79) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


barrels08  barrelsA08  charge120  charge240  city08  city08U  cityA08  \
0  15.695714         0.0        0.0        0.0      19      0.0        0   
1  29.964545         0.0        0.0        0.0       9      0.0        0   
2  12.207778         0.0        0.0        0.0      23      0.0        0   
3  29.964545         0.0        0.0        0.0      10      0.0        0   
4  17.347895         0.0        0.0        0.0      17      0.0        0   

   cityA08U  cityCD  cityE    ...     mfrCode  c240Dscr  charge240b  \
0       0.0     0.0    0.0    ...         NaN       NaN         0.0   
1       0.0     0.0    0.0    ...         NaN       NaN         0.0   
2       0.0     0.0    0.0    ...         NaN       NaN         0.0   
3       0.0     0.0    0.0    ...         NaN       NaN         0.0   
4       0.0     0.0    0.0    ...         NaN       NaN         0.0   

   c240bDscr                     createdOn                    modifiedOn  \
0        NaN  Tue Jan 01 00:00:00 EST 2013  Tue Jan 01 00:00:00 EST 2013   
1        NaN  Tue Jan 01 00:00:00 EST 2013  Tue Jan 01 00:00:00 EST 2013   
2        NaN  Tue Jan 01 00:00:00 EST 2013  Tue Jan 01 00:00:00 EST 2013   
3        NaN  Tue Jan 01 00:00:00 EST 2013  Tue Jan 01 00:00:00 EST 2013   
4        NaN  Tue Jan 01 00:00:00 EST 2013  Tue Jan 01 00:00:00 EST 2013   

   startStop  phevCity  phevHwy  phevComb  
0        NaN         0        0         0  
1        NaN         0        0         0  
2        NaN         0        0         0  
3        NaN         0        0         0  
4        NaN         0        0         0  

[5 rows x 83 columns]

In [6]:
df.columns

Index(['barrels08', 'barrelsA08', 'charge120', 'charge240', 'city08',
       'city08U', 'cityA08', 'cityA08U', 'cityCD', 'cityE', 'cityUF', 'co2',
       'co2A', 'co2TailpipeAGpm', 'co2TailpipeGpm', 'comb08', 'comb08U',
       'combA08', 'combA08U', 'combE', 'combinedCD', 'combinedUF', 'cylinders',
       'displ', 'drive', 'engId', 'eng_dscr', 'feScore', 'fuelCost08',
       'fuelCostA08', 'fuelType', 'fuelType1', 'ghgScore', 'ghgScoreA',
       'highway08', 'highway08U', 'highwayA08', 'highwayA08U', 'highwayCD',
       'highwayE', 'highwayUF', 'hlv', 'hpv', 'id', 'lv2', 'lv4', 'make',
       'model', 'mpgData', 'phevBlended', 'pv2', 'pv4', 'range', 'rangeCity',
       'rangeCityA', 'rangeHwy', 'rangeHwyA', 'trany', 'UCity', 'UCityA',
       'UHighway', 'UHighwayA', 'VClass', 'year', 'youSaveSpend', 'guzzler',
       'trans_dscr', 'tCharger', 'sCharger', 'atvType', 'fuelType2', 'rangeA',
       'evMotor', 'mfrCode', 'c240Dscr', 'charge240b', 'c240bDscr',
       'createdOn', 'modifiedOn

In [7]:
#df = df[['rangeHwyA', 'rangeCityA', 'make', 'model', 'year', 'mpgData', 'charge240', 'fuelCost08', 'fuelType1', ]]


elec_df = df[df['fuelType1'] == 'Electricity']

elec_df = elec_df[['range', 'rangeHwy', 'rangeCity', 'highway08', 'make', 'model', 'year',
                   'charge120', 'charge240', 'fuelCost08', 'fuelType1']]
# range = rounded, weighted avg of City (55%) and Hwy (45%) driving 
# highway08 = highway MPGe (equivalent for EVs to mpg)
# charge120/charge240 = time to charge an EV in hours at 120V/240V
# fuelCost08 = annual fuel cost based on 15k miles, 55% city driving, and price of fuel

#elec_df = elec_df[elec_df['year'] >= 2012] # only after 2012 did they have data on range

elec_df = elec_df.sort_values('year')


elec_df.head()

range  rangeHwy  rangeCity  highway08             make  \
23028     33    0.0000     0.0000         58        Chevrolet   
23029     72    0.0000     0.0000         28        Chevrolet   
23027     81    0.0000     0.0000         46            Honda   
23026     70    0.0000     0.0000         33         Plymouth   
23025     70    0.0000     0.0000         33            Dodge   
23024     55    0.0000     0.0000         44             Ford   
23023     50    0.0000     0.0000         54             Ford   
23022     81    0.0000     0.0000         46            Honda   
23020    105    0.0000     0.0000         39              GMC   
23019     55    0.0000     0.0000         94              GMC   
23018     65    0.0000     0.0000         52             Ford   
7138      90    0.0000     0.0000         91           Nissan   
7139      88    0.0000     0.0000         64           Toyota   
23017     50    0.0000     0.0000         54             Ford   
8143      88    0.0000     0.0000         64           Toyota   
8144      29    0.0000     0.0000         58             Ford   
8146      38    0.0000     0.0000         33             Ford   
23016     50    0.0000     0.0000         54             Ford   
8147      33    0.0000     0.0000         66           Nissan   
9212      95    0.0000     0.0000         69           Toyota   
9213      38    0.0000     0.0000         33             Ford   
10329     95    0.0000     0.0000         69           Toyota   
23030    100    0.0000     0.0000         94             MINI   
23031     73    0.0000     0.0000         92           Nissan   
23127     63    0.0000     0.0000         79            smart   
23128     63    0.0000     0.0000         79            smart   
24456     94    0.0000     0.0000         96              BMW   
25599    103   98.9000   107.0000         74           Toyota   
24457     88   93.5550    93.5550         68  CODA Automotive   
24768    265  266.7800   262.6900         90            Tesla   
...      ...       ...        ...        ...              ...   
35483    373  358.5551   384.3318        107            Tesla   
35484    348  346.9773   349.2432        104            Tesla   
35477    220  206.3000   230.5000        124            Tesla   
35485    326  321.9240   329.8471         96            Tesla   
36885    250  230.1587   266.7659         89       Volkswagen   
36886    250  230.1587   266.7659         89       Volkswagen   
36936    211  193.7000   225.5000         86             Ford   
36937    270  249.2000   286.4000         84             Ford   
36978     59   51.6000    64.3000        102            Kandi   
36939    300  277.1300   318.6100         90             Ford   
37002    153  136.4000   166.5000        102              BMW   
37003    259  235.1000   277.7000        108        Chevrolet   
36841    334  323.2000   342.6000         93            Tesla   
37004    149  131.3000   163.2000         99           Nissan   
36938    230  215.0000   242.4000         93             Ford   
36840    387  373.2000   398.3000        106            Tesla   
36715    371  356.3000   382.2000        101            Tesla   
36819    222  221.9408   222.7400         77             Audi   
37005    226  202.2000   245.0000         97           Nissan   
36719    303  289.0000   314.4000        106            Tesla   
36718    326  305.5000   342.5000        117            Tesla   
36717    300  289.0000   309.3000         83            Tesla   
36716    341  332.2000   348.0000         95            Tesla   
36714    315  299.0000   328.7000        107            Tesla   
36713    353  333.8000   369.5000        127            Tesla   
36594    208  188.0000   223.6000         72            Volvo   
36593    233  222.1000   241.9000         88         Polestar   
35870    110  101.9000   116.9000        100             MINI   
36820    218  221.4746   215.9764         78             Audi   
37006    215  192.5000   233.7000         

NOTE: Standard homes have 240V, but most wall outlets are only 120, so it is possible to have a level 2 charge at home but need a special plug-in station installed. 

## EV Range vs Annual Fuel Cost*

*Fuel Cost based on 15,000 miles travelled, 55% city driving, and prices for type of fuel (electric)

In [9]:
#gas_df = df[df['fuelType1'] == 'Gasoline']
#df['fuelType1'].unique()
gas_df = df[df['fuelType1'] != 'Electricity']
gas_df = gas_df[gas_df['year'] >= 2018]


gas_df['fuelCost08'].mean()

1820.2636419374617

In [15]:
scatter = alt.Chart(elec_df).mark_point(filled=True).encode(
    x = alt.X('fuelCost08', axis=alt.Axis(format='$.0f', title='Annual Fuel Cost')),
    y = alt.Y('range', axis=alt.Axis(title='Range (miles)')),
    color = alt.Color('year:O', scale=alt.Scale(scheme='yellowgreen', domain=[i for i in range(1998,2022)])),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).properties(title ='EV Range vs. Annual Fuel Cost').interactive()


gas_mean = alt.Chart(gas_df).mark_rule(color='red', strokeDash=[10,5]).encode(
    x = 'mean(fuelCost08):Q'
)

scatter + gas_mean

alt.LayerChart(...)

## Annual Fuel Cost vs. Model Year

In [17]:
alt.Chart(elec_df).mark_point(filled=True).encode(
    x = alt.X('year', axis=alt.Axis(format='') , scale = alt.Scale(domain=(1997,2022))),
    y = alt.Y('fuelCost08'),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).interactive()

alt.Chart(...)

## EV Range vs. Model Year

In [18]:
alt.Chart(elec_df).mark_point(filled=True).encode(
    x = alt.X('year', axis=alt.Axis(format='') , scale = alt.Scale(domain=(1997,2022))),
    y = alt.Y('range'),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).interactive()

alt.Chart(...)

The below chart is same as above, but also encodes make using color and shape

In [23]:
viable_df = elec_df[elec_df['range'] >= 100]
viable_df = viable_df[viable_df['year'] >= 2008]

alt.Chart(viable_df).mark_point(filled=True, size=50, opacity=0.6).encode(
    x = alt.X('year', axis=alt.Axis(format='', title='Model Year') , scale = alt.Scale(domain=(2006,2022))),
    y = alt.Y('range', axis=alt.Axis(title='Range (miles)')),
    color = alt.Color('make:N', sort='ascending', scale=alt.Scale(scheme='tableau20')),
    shape = alt.Shape('make:N', sort='ascending'),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).properties(title ='EV Range vs. Model Year').interactive()

alt.Chart(...)

Same as above, but limited to only EVs with a range > 150 miles.

In [20]:
usable_df = elec_df[elec_df['range'] > 150]

alt.Chart(usable_df).mark_point(filled=True).encode(
    x = alt.X('year', axis=alt.Axis(format='') , scale = alt.Scale(domain=(1997,2022))),
    y = alt.Y('range'),
    color = alt.Color('make:N'),
    shape = alt.Shape('make:N'),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).properties(title ='EV Range vs. Model Year').interactive()

alt.Chart(...)

Same chart, but only Tesla included

In [21]:
tesla_df = elec_df[elec_df['make'] == 'Tesla']

alt.Chart(tesla_df).mark_point(filled=True).encode(
    x = alt.X('year', axis=alt.Axis(format='') , scale = alt.Scale(domain=(1997,2022))),
    y = alt.Y('range'),
    color = alt.Color('make:N'),
    shape = alt.Shape('make:N'),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).interactive()

alt.Chart(...)

## Level 2 Charging Time vs. Range

In [22]:
alt.Chart(viable_df).mark_point(filled=True, size=50, opacity=0.6).encode(
    x = alt.X('range', axis=alt.Axis(title='Range (miles)')),
    y = alt.Y('charge240', axis=alt.Axis(title='Level 2 Charging Time (hours)')),
    color = alt.Color('make:N', sort='ascending', scale=alt.Scale(scheme='tableau20')),
    shape = alt.Shape('make:N', sort='ascending'),
    tooltip = ['make', 'model', 'year', 'fuelCost08', 'range', 'charge240']
).properties(title ='Level 2 Charging Time vs. EV Range').interactive()

alt.Chart(...)